In [39]:
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
%matplotlib inline 
import re
from datetime import datetime

In [40]:
import warnings
warnings.filterwarnings('ignore')
warnings.warn("this will not show")

In [41]:
df = pd.read_json('scout_car.json', lines=True)

In [42]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 15919 entries, 0 to 15918
Data columns (total 54 columns):
 #   Column                         Non-Null Count  Dtype  
---  ------                         --------------  -----  
 0   url                            15919 non-null  object 
 1   make_model                     15919 non-null  object 
 2   short_description              15873 non-null  object 
 3   body_type                      15859 non-null  object 
 4   price                          15919 non-null  int64  
 5   vat                            11406 non-null  object 
 6   km                             15919 non-null  object 
 7   registration                   15919 non-null  object 
 8   prev_owner                     9091 non-null   object 
 9   kW                             0 non-null      float64
 10  hp                             15919 non-null  object 
 11  Type                           15917 non-null  object 
 12  Previous Owners                9279 non-null  

In [43]:
colm=list(df.columns)
colm

['url',
 'make_model',
 'short_description',
 'body_type',
 'price',
 'vat',
 'km',
 'registration',
 'prev_owner',
 'kW',
 'hp',
 'Type',
 'Previous Owners',
 'Next Inspection',
 'Inspection new',
 'Warranty',
 'Full Service',
 'Non-smoking Vehicle',
 'null',
 'Make',
 'Model',
 'Offer Number',
 'First Registration',
 'Body Color',
 'Paint Type',
 'Body Color Original',
 'Upholstery',
 'Body',
 'Nr. of Doors',
 'Nr. of Seats',
 'Model Code',
 'Gearing Type',
 'Displacement',
 'Cylinders',
 'Weight',
 'Drive chain',
 'Fuel',
 'Consumption',
 'CO2 Emission',
 'Emission Class',
 '\nComfort & Convenience\n',
 '\nEntertainment & Media\n',
 '\nExtras\n',
 '\nSafety & Security\n',
 'description',
 'Emission Label',
 'Gears',
 'Country version',
 'Electricity consumption',
 'Last Service Date',
 'Other Fuel Types',
 'Availability',
 'Last Timing Belt Service Date',
 'Available from']

In [44]:
df.isnull().sum()*100/df.shape[0]

url                                0.000000
make_model                         0.000000
short_description                  0.288963
body_type                          0.376908
price                              0.000000
vat                               28.349771
km                                 0.000000
registration                       0.000000
prev_owner                        42.892141
kW                               100.000000
hp                                 0.000000
Type                               0.012564
Previous Owners                   41.711163
Next Inspection                   77.793831
Inspection new                    75.299956
Warranty                          34.047365
Full Service                      48.395000
Non-smoking Vehicle               54.915510
null                               0.000000
Make                               0.000000
Model                              0.000000
Offer Number                      19.944720
First Registration              

In [45]:
def col_to_drop(df, limit):
    null_rate = df.isnull().sum()*100/df.shape[0]
    return null_rate.loc[lambda x: x> limit]

# round(car.isnull().sum()/car.shape[0]*100
# sort_values(ascending=False)>65.0
# ((cars.isna().sum()/cars.shape[0])>0.35)
#  [df.columns[i] for i in range(54) if df[df.columns[i]].isnull().sum() > df.shape[0]*0.35]
#  missing_lst = [i if (scout[i].isnull().sum()/scout[i].shape[0])*100 < 65 else '' for  i in scout.columns]

In [46]:
col_to_drop(df, 90)

kW                               100.000000
Electricity consumption           99.139393
Last Service Date                 96.444500
Other Fuel Types                  94.472015
Availability                      96.011056
Last Timing Belt Service Date     99.899491
Available from                    98.291350
dtype: float64

**I drop the columns with more than %90 missing value**

In [47]:
df.drop(['Available from', 'Last Timing Belt Service Date', 'Availability', 'Last Service Date', 'kW', 'Other Fuel Types', 'Electricity consumption'], axis=1, inplace=True)

In [48]:
df.prev_owner.value_counts(dropna=False)

1 previous owner     8294
NaN                  6828
2 previous owners     778
3 previous owners      17
4 previous owners       2
Name: prev_owner, dtype: int64

In [49]:
df['Previous Owners'].value_counts(dropna=False)

TypeError: unhashable type: 'list'

Exception ignored in: 'pandas._libs.index.IndexEngine._call_map_locations'
Traceback (most recent call last):
  File "pandas\_libs\hashtable_class_helper.pxi", line 1652, in pandas._libs.hashtable.PyObjectHashTable.map_locations
TypeError: unhashable type: 'list'


\n1\n                                                                                        8101
NaN                                                                                          6640
\n2\n                                                                                         766
\n0\n                                                                                         163
\n3\n                                                                                          17
                                                                                             ... 
[\n1\n, \n96 g CO2/km (comb)\n]                                                                 1
[\n1\n, \n181 g CO2/km (comb)\n]                                                                1
[\n1\n, \n, 6 l/100 km (comb), \n, 8 l/100 km (city), \n, 4.9 l/100 km (country), \n]           1
[\n1\n, \n, 6.7 l/100 km (comb), \n, 8.6 l/100 km (city), \n, 5.6 l/100 km (country), \n]       1
[\n1\n, \n102 g CO2/

**The data in the Previous Owners column is dirtier than prew_owner column. Thus drop Previous Owners column.**

In [50]:
df.drop(['Previous Owners'], inplace = True, axis = 'columns')

In [51]:
col_to_drop(df, 35)

prev_owner             42.892141
Next Inspection        77.793831
Inspection new         75.299956
Full Service           48.395000
Non-smoking Vehicle    54.915510
Paint Type             36.258559
Model Code             68.729192
Cylinders              35.680633
Weight                 43.809285
Drive chain            43.080596
Emission Label         74.967021
Country version        52.346253
dtype: float64

In [52]:
df.prev_owner

0        2 previous owners
1                     None
2         1 previous owner
3         1 previous owner
4         1 previous owner
               ...        
15914                 None
15915     1 previous owner
15916     1 previous owner
15917                 None
15918     1 previous owner
Name: prev_owner, Length: 15919, dtype: object

In [53]:
df.prev_owner = df.prev_owner.str.replace(' previous owner', '').str.replace('s','')

In [54]:
df.prev_owner.fillna(method = 'bfill', inplace = True)

In [55]:
df.prev_owner.value_counts(dropna=False)

1    14692
2     1187
3       38
4        2
Name: prev_owner, dtype: int64

**Inspect the body_type and Body columns if the same drop the useless one and fill the missing value of the other**

In [56]:
df.Body.value_counts(dropna=False)

TypeError: unhashable type: 'list'

Exception ignored in: 'pandas._libs.index.IndexEngine._call_map_locations'
Traceback (most recent call last):
  File "pandas\_libs\hashtable_class_helper.pxi", line 1652, in pandas._libs.hashtable.PyObjectHashTable.map_locations
TypeError: unhashable type: 'list'


[\n, Sedans, \n]           7903
[\n, Station wagon, \n]    3553
[\n, Compact, \n]          3153
[\n, Van, \n]               783
[\n, Other, \n]             290
[\n, Transporter, \n]        88
NaN                          60
[\n, Off-Road, \n]           56
[\n, Coupe, \n]              25
[\n, Convertible, \n]         8
Name: Body, dtype: int64

In [57]:
df.body_type.value_counts(dropna=False)

Sedans           7903
Station wagon    3553
Compact          3153
Van               783
Other             290
Transporter        88
NaN                60
Off-Road           56
Coupe              25
Convertible         8
Name: body_type, dtype: int64

In [58]:
df.drop(['Body'], inplace=True, axis=1)

In [59]:
df.groupby('make_model')['body_type'].value_counts(dropna = False)

make_model      body_type    
Audi A1         Sedans           1538
                Compact          1039
                Station wagon      21
                Other              13
                Coupe               2
                Van                 1
Audi A2         Off-Road            1
Audi A3         Sedans           2598
                Station wagon     282
                Compact           182
                Other              16
                Convertible         8
                NaN                 7
                Coupe               4
Opel Astra      Station wagon    1211
                Sedans           1053
                Compact           185
                Other              67
                NaN                 7
                Coupe               2
                Off-Road            1
Opel Corsa      Compact          1230
                Sedans            875
                Other              87
                Coupe              13
                Tran

In [60]:
fill_most(df, 'make_model', 'body_type')

NameError: name 'fill_most' is not defined

In [61]:
df['body_type'] = df['body_type'].fillna(df.groupby('make_model')['body_type'].apply(lambda x: x.fillna(x.mode()[0])))

In [62]:
df.body_type.isnull().sum()

0

In [63]:
df.groupby('make_model')['body_type'].apply(lambda x: x.fillna(x.mode()[0]))

0        Sedans
1        Sedans
2        Sedans
3        Sedans
4        Sedans
          ...  
15914       Van
15915       Van
15916       Van
15917       Van
15918       Van
Name: body_type, Length: 15919, dtype: object

In [64]:
df.body_type.value_counts(dropna=False)

Sedans           7925
Station wagon    3563
Compact          3155
Van               809
Other             290
Transporter        88
Off-Road           56
Coupe              25
Convertible         8
Name: body_type, dtype: int64

**Write a function to fill the missing values with most recurring make_model in the DF**

In [65]:
def fill_most(df, base_col, col):
    for group in list(df[base_col].unique()):
        grp_inx= list(df[df[base_col] == group][col].index)
        df[col].iloc[grp_inx] = df[col].iloc[grp_inx].fillna(df[df[base_col]== group])

In [66]:
fill_most(df, 'make_model', 'body_type')

TypeError: "value" parameter must be a scalar, dict or Series, but you passed a "DataFrame"

In [67]:
df.body_type.isnull().sum()

0

In [68]:
list(df[df['make_model'] == 'Audi A3']['body_type'].index)

[2615,
 2616,
 2617,
 2618,
 2619,
 2620,
 2621,
 2622,
 2623,
 2624,
 2625,
 2626,
 2627,
 2628,
 2629,
 2630,
 2631,
 2632,
 2633,
 2634,
 2635,
 2636,
 2637,
 2638,
 2639,
 2640,
 2641,
 2642,
 2643,
 2644,
 2645,
 2646,
 2647,
 2648,
 2649,
 2650,
 2651,
 2652,
 2653,
 2654,
 2655,
 2656,
 2657,
 2658,
 2659,
 2660,
 2661,
 2662,
 2663,
 2664,
 2665,
 2666,
 2667,
 2668,
 2669,
 2670,
 2671,
 2672,
 2673,
 2674,
 2675,
 2676,
 2677,
 2678,
 2679,
 2680,
 2681,
 2682,
 2683,
 2684,
 2685,
 2686,
 2687,
 2688,
 2689,
 2690,
 2691,
 2692,
 2693,
 2694,
 2695,
 2696,
 2697,
 2698,
 2699,
 2700,
 2701,
 2702,
 2703,
 2704,
 2705,
 2706,
 2707,
 2708,
 2709,
 2710,
 2711,
 2712,
 2713,
 2714,
 2715,
 2716,
 2717,
 2718,
 2719,
 2720,
 2721,
 2722,
 2723,
 2724,
 2725,
 2726,
 2727,
 2728,
 2729,
 2730,
 2731,
 2732,
 2733,
 2734,
 2735,
 2736,
 2737,
 2738,
 2739,
 2740,
 2741,
 2742,
 2743,
 2744,
 2745,
 2746,
 2747,
 2748,
 2749,
 2750,
 2751,
 2752,
 2753,
 2754,
 2755,
 2756,
 2757,

In [69]:
df['Inspection new'].isnull().sum()*100/len(df['Inspection new'])

75.29995602738866

In [70]:
df['Next Inspection'].value_counts(dropna=True)

TypeError: unhashable type: 'list'

Exception ignored in: 'pandas._libs.index.IndexEngine._call_map_locations'
Traceback (most recent call last):
  File "pandas\_libs\hashtable_class_helper.pxi", line 1652, in pandas._libs.hashtable.PyObjectHashTable.map_locations
TypeError: unhashable type: 'list'


\n04/2022\n                                                                                      62
\n03/2021\n                                                                                      38
\n03/2022\n                                                                                      36
\n06/2021\n                                                                                      34
\n01/2022\n                                                                                      32
                                                                                                 ..
[\n03/2022\n, \n, 5 l/100 km (comb), \n, 6.3 l/100 km (city), \n, 4.2 l/100 km (country), \n]     1
[\n11/2021\n, \n111 g CO2/km (comb)\n]                                                            1
[\n09/2019\n, \n99 g CO2/km (comb)\n]                                                             1
[\n01/2020\n, \n, 6.1 l/100 km (comb), \n, 8 l/100 km (city), \n, 5.1 l/100 km (country), \n]     1


In [71]:
nxtins= [''.join(item).strip() if type(item)== list else item for item in df['Next Inspection']]

In [72]:
df['Next Inspection'] = pd.DataFrame(nxtins)

In [73]:
df['Next Inspection']

0         06/2021\n\n99 g CO2/km (comb)
1                                   NaN
2                                   NaN
3                                   NaN
4                                   NaN
                      ...              
15914                               NaN
15915    01/2022\n\n168 g CO2/km (comb)
15916                               NaN
15917                               NaN
15918                               NaN
Name: Next Inspection, Length: 15919, dtype: object

In [74]:
df['\nComfort & Convenience\n'][0]

['Air conditioning',
 'Armrest',
 'Automatic climate control',
 'Cruise control',
 'Electrical side mirrors',
 'Hill Holder',
 'Leather steering wheel',
 'Light sensor',
 'Multi-function steering wheel',
 'Navigation system',
 'Park Distance Control',
 'Parking assist system sensors rear',
 'Power windows',
 'Rain sensor',
 'Seat heating',
 'Start-stop system']

In [75]:
df.head()

url make_model  \
0  https://www.autoscout24.com//offers/audi-a1-sp...    Audi A1   
1  https://www.autoscout24.com//offers/audi-a1-1-...    Audi A1   
2  https://www.autoscout24.com//offers/audi-a1-sp...    Audi A1   
3  https://www.autoscout24.com//offers/audi-a1-1-...    Audi A1   
4  https://www.autoscout24.com//offers/audi-a1-sp...    Audi A1   

                                   short_description body_type  price  \
0        Sportback 1.4 TDI S-tronic Xenon Navi Klima    Sedans  15770   
1                                     1.8 TFSI sport    Sedans  14500   
2  Sportback 1.6 TDI S tronic Einparkhilfe plus+m...    Sedans  14640   
3                            1.4 TDi Design S tronic    Sedans  14500   
4  Sportback 1.4 TDI S-Tronic S-Line Ext. admired...    Sedans  16790   

                vat         km registration prev_owner      hp  ...  \
0    VAT deductible  56,013 km      01/2016          2   66 kW  ...   
1  Price negotiable  80,000 km      03/2017          1  141 kW  ...   
2    VAT deductible  83,450 km      02/2016          1   85 kW  ...   
3              None  73,000 km      08/2016          1   66 kW  ...   
4              None  16,200 km      05/2016          1   66 kW  ...   

                CO2 Emission Emission Class  \
0   [\n99 g CO2/km (comb)\n]   [\nEuro 6\n]   
1  [\n129 g CO2/km (comb)\n]   [\nEuro 6\n]   
2   [\n99 g CO2/km (comb)\n]   [\nEuro 6\n]   
3   [\n99 g CO2/km (comb)\n]   [\nEuro 6\n]   
4  [\n109 g CO2/km (comb)\n]   [\nEuro 6\n]   

                           \nComfort & Convenience\n  \
0  [Air conditioning, Armrest, Automatic climate ...   
1  [Air conditioning, Automatic climate control, ...   
2  [Air conditioning, Cruise control, Electrical ...   
3  [Air suspension, Armrest, Auxiliary heating, E...   
4  [Air conditioning, Armrest, Automatic climate ...   

                           \nEntertainment & Media\n  \
0  [Bluetooth, Hands-free equipment, On-board com...   
1  [Bluetooth, Hands-free equipment, On-board com...   
2                           [MP3, On-board computer]   
3  [Bluetooth, CD player, Hands-free equipment, M...   
4  [Bluetooth, CD player, Hands-free equipment, M...   

                                          \nExtras\n  \
0  [Alloy wheels, Catalytic Converter, Voice Cont...   
1  [Alloy wheels, Sport seats, Sport suspension, ...   
2                      [Alloy wheels, Voice Control]   
3         [Alloy wheels, Sport seats, Voice Control]   
4  [Alloy wheels, Sport package, Sport suspension...   

                               \nSafety & Security\n  \
0  [ABS, Central door lock, Daytime running light...   
1  [ABS, Central door lock, Central door lock wit...   
2  [ABS, Central door lock, Daytime running light...   
3  [ABS, Alarm system, Central door lock with rem...   
4  [ABS, Central door lock, Driver-side airbag, E...   

                                         description   Emission Label  \
0  [\n, Sicherheit:,  , Deaktivierung für Beifahr...              NaN   
1  [\nLangstreckenfahrzeug daher die hohe Kilomet...  [\n4 (Green)\n]   
2  [\n, Fahrzeug-Nummer: AM-95365,  , Ehem. UPE 2...  [\n4 (Green)\n]   
3  [\nAudi A1: , - 1e eigenaar , - Perfecte staat...              NaN   
4  [\n, Technik & Sicherheit:, Xenon plus, Klimaa...              NaN   

     Gears Country version  
0      NaN             NaN  
1  [\n7\n]             NaN  
2      NaN             NaN  
3  [\n6\n]             NaN  
4      NaN   [\nGermany\n]  

[5 rows x 45 columns]

In [76]:
df['Type'].value_counts()

TypeError: unhashable type: 'list'

Exception ignored in: 'pandas._libs.index.IndexEngine._call_map_locations'
Traceback (most recent call last):
  File "pandas\_libs\hashtable_class_helper.pxi", line 1652, in pandas._libs.hashtable.PyObjectHashTable.map_locations
TypeError: unhashable type: 'list'


[, Used, , Diesel (Particulate Filter)]                                                                                            3475
[, Used, , Diesel]                                                                                                                 2516
[, Used, , Gasoline]                                                                                                               2367
[, Used, , Super 95]                                                                                                               1818
[, Pre-registered, , Super 95]                                                                                                      500
                                                                                                                                   ... 
[, Pre-registered, , Regular/Benzine 91 / Super 95 / Regular/Benzine E10 91 / Super E10 95 / Super Plus 98 / Super Plus E10 98]       1
[, Pre-registered, , CNG]                       

In [77]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 15919 entries, 0 to 15918
Data columns (total 45 columns):
 #   Column                   Non-Null Count  Dtype 
---  ------                   --------------  ----- 
 0   url                      15919 non-null  object
 1   make_model               15919 non-null  object
 2   short_description        15873 non-null  object
 3   body_type                15919 non-null  object
 4   price                    15919 non-null  int64 
 5   vat                      11406 non-null  object
 6   km                       15919 non-null  object
 7   registration             15919 non-null  object
 8   prev_owner               15919 non-null  object
 9   hp                       15919 non-null  object
 10  Type                     15917 non-null  object
 11  Next Inspection          3535 non-null   object
 12  Inspection new           3932 non-null   object
 13  Warranty                 10499 non-null  object
 14  Full Service             8215 non-null

In [78]:
df.drop(['Previous Owners'], inplace=True, axis=1)

KeyError: "['Previous Owners'] not found in axis"

In [79]:
df.head()

url make_model  \
0  https://www.autoscout24.com//offers/audi-a1-sp...    Audi A1   
1  https://www.autoscout24.com//offers/audi-a1-1-...    Audi A1   
2  https://www.autoscout24.com//offers/audi-a1-sp...    Audi A1   
3  https://www.autoscout24.com//offers/audi-a1-1-...    Audi A1   
4  https://www.autoscout24.com//offers/audi-a1-sp...    Audi A1   

                                   short_description body_type  price  \
0        Sportback 1.4 TDI S-tronic Xenon Navi Klima    Sedans  15770   
1                                     1.8 TFSI sport    Sedans  14500   
2  Sportback 1.6 TDI S tronic Einparkhilfe plus+m...    Sedans  14640   
3                            1.4 TDi Design S tronic    Sedans  14500   
4  Sportback 1.4 TDI S-Tronic S-Line Ext. admired...    Sedans  16790   

                vat         km registration prev_owner      hp  ...  \
0    VAT deductible  56,013 km      01/2016          2   66 kW  ...   
1  Price negotiable  80,000 km      03/2017          1  141 kW  ...   
2    VAT deductible  83,450 km      02/2016          1   85 kW  ...   
3              None  73,000 km      08/2016          1   66 kW  ...   
4              None  16,200 km      05/2016          1   66 kW  ...   

                CO2 Emission Emission Class  \
0   [\n99 g CO2/km (comb)\n]   [\nEuro 6\n]   
1  [\n129 g CO2/km (comb)\n]   [\nEuro 6\n]   
2   [\n99 g CO2/km (comb)\n]   [\nEuro 6\n]   
3   [\n99 g CO2/km (comb)\n]   [\nEuro 6\n]   
4  [\n109 g CO2/km (comb)\n]   [\nEuro 6\n]   

                           \nComfort & Convenience\n  \
0  [Air conditioning, Armrest, Automatic climate ...   
1  [Air conditioning, Automatic climate control, ...   
2  [Air conditioning, Cruise control, Electrical ...   
3  [Air suspension, Armrest, Auxiliary heating, E...   
4  [Air conditioning, Armrest, Automatic climate ...   

                           \nEntertainment & Media\n  \
0  [Bluetooth, Hands-free equipment, On-board com...   
1  [Bluetooth, Hands-free equipment, On-board com...   
2                           [MP3, On-board computer]   
3  [Bluetooth, CD player, Hands-free equipment, M...   
4  [Bluetooth, CD player, Hands-free equipment, M...   

                                          \nExtras\n  \
0  [Alloy wheels, Catalytic Converter, Voice Cont...   
1  [Alloy wheels, Sport seats, Sport suspension, ...   
2                      [Alloy wheels, Voice Control]   
3         [Alloy wheels, Sport seats, Voice Control]   
4  [Alloy wheels, Sport package, Sport suspension...   

                               \nSafety & Security\n  \
0  [ABS, Central door lock, Daytime running light...   
1  [ABS, Central door lock, Central door lock wit...   
2  [ABS, Central door lock, Daytime running light...   
3  [ABS, Alarm system, Central door lock with rem...   
4  [ABS, Central door lock, Driver-side airbag, E...   

                                         description   Emission Label  \
0  [\n, Sicherheit:,  , Deaktivierung für Beifahr...              NaN   
1  [\nLangstreckenfahrzeug daher die hohe Kilomet...  [\n4 (Green)\n]   
2  [\n, Fahrzeug-Nummer: AM-95365,  , Ehem. UPE 2...  [\n4 (Green)\n]   
3  [\nAudi A1: , - 1e eigenaar , - Perfecte staat...              NaN   
4  [\n, Technik & Sicherheit:, Xenon plus, Klimaa...              NaN   

     Gears Country version  
0      NaN             NaN  
1  [\n7\n]             NaN  
2      NaN             NaN  
3  [\n6\n]             NaN  
4      NaN   [\nGermany\n]  

[5 rows x 45 columns]

In [80]:
df['Type'].fillna(value = '[, Used, , Diesel (Particulate Filter)]', inplace=True)

In [81]:
df['Type'].isnull().sum()

0

In [82]:
df['Type'] = df['Type'].apply(lambda x: x[3])

In [83]:
df['Type']

0                          Diesel (Particulate Filter)
1                                             Gasoline
2                          Diesel (Particulate Filter)
3                          Diesel (Particulate Filter)
4                          Diesel (Particulate Filter)
                             ...                      
15914                      Diesel (Particulate Filter)
15915    Super 95 / Super Plus 98 (Particulate Filter)
15916                                           Diesel
15917                                           Diesel
15918                                         Super 95
Name: Type, Length: 15919, dtype: object

**Next Inspection**

In [84]:
df['Next Inspection']

0         06/2021\n\n99 g CO2/km (comb)
1                                   NaN
2                                   NaN
3                                   NaN
4                                   NaN
                      ...              
15914                               NaN
15915    01/2022\n\n168 g CO2/km (comb)
15916                               NaN
15917                               NaN
15918                               NaN
Name: Next Inspection, Length: 15919, dtype: object

In [85]:
df['Next Inspection']. isnull().sum()

12384

In [86]:
df['Next Inspection']. notnull().sum()

3535

In [87]:
pd.set_option("max_rows", None)
# pd.reset_option(“max_columns”)

In [88]:
df['Next Inspection']

0                            06/2021\n\n99 g CO2/km (comb)
1                                                      NaN
2                                                      NaN
3                                                      NaN
4                                                      NaN
5                                                      NaN
6                                                      NaN
7                                                      NaN
8                            02/2020\n\n97 g CO2/km (comb)
9                                                      NaN
10                                                     NaN
11                                                     NaN
12                          09/2019\n\n112 g CO2/km (comb)
13                                                     NaN
14                           10/2019\n\n99 g CO2/km (comb)
15                           04/2020\n\n97 g CO2/km (comb)
16                                                     N

In [89]:
df['Next Inspection'][df['Next Inspection'].notnull()].head(10)

0      06/2021\n\n99 g CO2/km (comb)
8      02/2020\n\n97 g CO2/km (comb)
12    09/2019\n\n112 g CO2/km (comb)
14     10/2019\n\n99 g CO2/km (comb)
15     04/2020\n\n97 g CO2/km (comb)
18                       \n07/2020\n
22    12/2019\n\n112 g CO2/km (comb)
31     05/2019\n\n95 g CO2/km (comb)
37     07/2019\n\n97 g CO2/km (comb)
38     10/2019\n\n97 g CO2/km (comb)
Name: Next Inspection, dtype: object

In [90]:
type(df['Next Inspection'][0])

str

In [91]:
df['Next Inspection'].value_counts(dropna=False)

NaN                                                                            12384
\n04/2022\n                                                                       62
\n03/2021\n                                                                       38
\n03/2022\n                                                                       36
\n06/2021\n                                                                       34
\n01/2022\n                                                                       32
\n04/2021\n                                                                       29
06/2021\n\nEuro 6                                                                 29
08/2021\n\n135 g CO2/km (comb)                                                    28
\n05/2021\n                                                                       27
\n05/2022\n                                                                       27
\n03/2020\n                                                      

In [92]:
nxins = [''.join(item).strip() if type(item)==list else item for item in df['Next Inspection']]

In [93]:
df['Next Inspection'] = pd.DataFrame(nxins)

In [94]:
df['Next Inspection'].value_counts(dropna=False)

NaN                                                                            12384
\n04/2022\n                                                                       62
\n03/2021\n                                                                       38
\n03/2022\n                                                                       36
\n06/2021\n                                                                       34
\n01/2022\n                                                                       32
\n04/2021\n                                                                       29
06/2021\n\nEuro 6                                                                 29
08/2021\n\n135 g CO2/km (comb)                                                    28
\n05/2021\n                                                                       27
\n05/2022\n                                                                       27
\n03/2020\n                                                      

In [95]:
type(df['Next Inspection'][0])

str

In [96]:
df['Next_Inspection']= df['Next Inspection'].str.extract('(\d\d/\d\d\d\d)')

In [97]:
df['Next Inspection'].value_counts(dropna=False)

NaN                                                                            12384
\n04/2022\n                                                                       62
\n03/2021\n                                                                       38
\n03/2022\n                                                                       36
\n06/2021\n                                                                       34
\n01/2022\n                                                                       32
\n04/2021\n                                                                       29
06/2021\n\nEuro 6                                                                 29
08/2021\n\n135 g CO2/km (comb)                                                    28
\n05/2021\n                                                                       27
\n05/2022\n                                                                       27
\n03/2020\n                                                      

In [98]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 15919 entries, 0 to 15918
Data columns (total 46 columns):
 #   Column                   Non-Null Count  Dtype 
---  ------                   --------------  ----- 
 0   url                      15919 non-null  object
 1   make_model               15919 non-null  object
 2   short_description        15873 non-null  object
 3   body_type                15919 non-null  object
 4   price                    15919 non-null  int64 
 5   vat                      11406 non-null  object
 6   km                       15919 non-null  object
 7   registration             15919 non-null  object
 8   prev_owner               15919 non-null  object
 9   hp                       15919 non-null  object
 10  Type                     15919 non-null  object
 11  Next Inspection          3535 non-null   object
 12  Inspection new           3932 non-null   object
 13  Warranty                 10499 non-null  object
 14  Full Service             8215 non-null

**'Inspection New'**

In [99]:
df['Inspection new']

0                                    [\nYes\n, \nEuro 6\n]
1                                                      NaN
2                                                      NaN
3                                                      NaN
4                       [\nYes\n, \n109 g CO2/km (comb)\n]
5                                                      NaN
6                        [\nYes\n, \n98 g CO2/km (comb)\n]
7                        [\nYes\n, \n97 g CO2/km (comb)\n]
8                                                      NaN
9                                                      NaN
10                                                     NaN
11                      [\nYes\n, \n112 g CO2/km (comb)\n]
12                                                     NaN
13                                                     NaN
14                                                     NaN
15                                                     NaN
16                                                     N

In [100]:
df['Inspection new'][df['Inspection new'].notnull()]='Yes'

In [101]:
df['Inspection new'][df['Inspection new'].notnull()]

0        Yes
4        Yes
6        Yes
7        Yes
11       Yes
21       Yes
26       Yes
32       Yes
35       Yes
36       Yes
40       Yes
41       Yes
42       Yes
48       Yes
49       Yes
61       Yes
63       Yes
64       Yes
72       Yes
73       Yes
75       Yes
78       Yes
79       Yes
82       Yes
83       Yes
85       Yes
92       Yes
117      Yes
120      Yes
124      Yes
128      Yes
133      Yes
135      Yes
136      Yes
137      Yes
143      Yes
146      Yes
147      Yes
148      Yes
149      Yes
153      Yes
154      Yes
156      Yes
160      Yes
161      Yes
163      Yes
164      Yes
167      Yes
178      Yes
179      Yes
180      Yes
182      Yes
183      Yes
184      Yes
185      Yes
186      Yes
188      Yes
189      Yes
192      Yes
202      Yes
204      Yes
207      Yes
211      Yes
212      Yes
213      Yes
215      Yes
216      Yes
217      Yes
219      Yes
222      Yes
223      Yes
234      Yes
235      Yes
236      Yes
237      Yes
238      Yes
239      Yes

In [102]:
df['Inspection new'][df['Inspection new'].isnull()]='No'

In [103]:
df['Inspection new'].value_counts(dropna=False)

No     11987
Yes     3932
Name: Inspection new, dtype: int64

In [104]:
df['Inspection_New_Bool'] = df['Inspection new'].str.contains('Yes', na=False)*1

In [105]:
df['Inspection_New_Bool'].value_counts(dropna=False)

0    11987
1     3932
Name: Inspection_New_Bool, dtype: int64

**Paint Type**

In [106]:
df['Paint Type'].isnull().sum()*100/len(df['Paint Type'])

36.258558954708214

In [107]:
df['Paint Type'] = df['Paint Type'].str[0].str.strip('\n')

In [108]:
df['Paint Type'].value_counts(dropna=False)

Metallic       9794
NaN            5772
Uni/basic       347
Perl effect       6
Name: Paint Type, dtype: int64

**Country Version**

In [109]:
df['Country version'].isnull().sum()*100/len(df['Country version'])

52.34625290533325

In [110]:
df['Country version'].value_counts(dropna=False)

TypeError: unhashable type: 'list'

Exception ignored in: 'pandas._libs.index.IndexEngine._call_map_locations'
Traceback (most recent call last):
  File "pandas\_libs\hashtable_class_helper.pxi", line 1652, in pandas._libs.hashtable.PyObjectHashTable.map_locations
TypeError: unhashable type: 'list'


NaN                     8333
[\nGermany\n]           4502
[\nItaly\n]             1038
[\nEuropean Union\n]     507
[\nNetherlands\n]        464
[\nSpain\n]              325
[\nBelgium\n]            314
[\nAustria\n]            208
[\nCzech Republic\n]      52
[\nPoland\n]              49
[\nFrance\n]              38
[\nDenmark\n]             33
[\nHungary\n]             28
[\nJapan\n]                8
[\nSlovakia\n]             4
[\nCroatia\n]              4
[\nSweden\n]               3
[\nRomania\n]              2
[\nBulgaria\n]             2
[\nSerbia\n]               1
[\nLuxembourg\n]           1
[\nSwitzerland\n]          1
[\nSlovenia\n]             1
[\nEgypt\n]                1
Name: Country version, dtype: int64

In [111]:
df['Country version'] = df['Country version'].str[0].str.strip('\n')

In [112]:
df['Cylinders'] = df['Cylinders'].str[0].str.strip('\n')

In [113]:
df['Warranty']

0                                  [\n, \n, \n4 (Green)\n]
1                                                      NaN
2                         [\n, \n, \n99 g CO2/km (comb)\n]
3                                                      NaN
4                                     [\n, \n, \nEuro 6\n]
5                                                      NaN
6                                                      NaN
7                                     [\n, \n, \nEuro 6\n]
8                              [\n12 months\n, \nEuro 6\n]
9                                             \n3 months\n
10                                                     NaN
11                                    [\n, \n, \nEuro 6\n]
12                                    [\n, \n, \nEuro 6\n]
13                                           \n12 months\n
14                                                     NaN
15                             [\n12 months\n, \nEuro 6\n]
16                                                     N

In [114]:
warr = df['Warranty'].str.extract('(\d{1,2} months)')

In [115]:
df['Warranty'] = warr

In [116]:
df['Warranty']

0              NaN
1              NaN
2              NaN
3              NaN
4              NaN
5              NaN
6              NaN
7              NaN
8              NaN
9         3 months
10             NaN
11             NaN
12             NaN
13       12 months
14             NaN
15             NaN
16             NaN
17             NaN
18             NaN
19             NaN
20             NaN
21             NaN
22             NaN
23             NaN
24             NaN
25             NaN
26             NaN
27             NaN
28             NaN
29             NaN
30       12 months
31             NaN
32             NaN
33             NaN
34             NaN
35             NaN
36             NaN
37             NaN
38             NaN
39             NaN
40             NaN
41             NaN
42             NaN
43             NaN
44             NaN
45             NaN
46             NaN
47             NaN
48             NaN
49             NaN
50             NaN
51             NaN
52          

In [117]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 15919 entries, 0 to 15918
Data columns (total 47 columns):
 #   Column                   Non-Null Count  Dtype 
---  ------                   --------------  ----- 
 0   url                      15919 non-null  object
 1   make_model               15919 non-null  object
 2   short_description        15873 non-null  object
 3   body_type                15919 non-null  object
 4   price                    15919 non-null  int64 
 5   vat                      11406 non-null  object
 6   km                       15919 non-null  object
 7   registration             15919 non-null  object
 8   prev_owner               15919 non-null  object
 9   hp                       15919 non-null  object
 10  Type                     15919 non-null  object
 11  Next Inspection          3535 non-null   object
 12  Inspection new           15919 non-null  object
 13  Warranty                 2057 non-null   object
 14  Full Service             8215 non-null

In [118]:
df['Full Service']

0                                                 [\n, \n]
1                                                      NaN
2                                                      NaN
3                         [\n, \n, \n99 g CO2/km (comb)\n]
4                                  [\n, \n, \n4 (Green)\n]
5                         [\n, \n, \n92 g CO2/km (comb)\n]
6                                     [\n, \n, \nEuro 6\n]
7                                  [\n, \n, \n4 (Green)\n]
8                                                      NaN
9                                                      NaN
10                                                      \n
11                                 [\n, \n, \n4 (Green)\n]
12                                                     NaN
13                                                     NaN
14                                                     NaN
15                                                [\n, \n]
16                                                     N

In [119]:
df.drop('Full Service', axis=1, inplace=True)

In [120]:
df['Non-smoking Vehicle']

0                                                 [\n, \n]
1                                                      NaN
2                                                      NaN
3                                     [\n, \n, \nEuro 6\n]
4                                                 [\n, \n]
5                                     [\n, \n, \nEuro 6\n]
6                                  [\n, \n, \n4 (Green)\n]
7                                                      NaN
8                                                      NaN
9                                                      NaN
10                                                     NaN
11                                                [\n, \n]
12                                 [\n, \n, \n4 (Green)\n]
13                                                     NaN
14                                                     NaN
15                                                [\n, \n]
16                                                     N

In [121]:
df.drop('Non-smoking Vehicle', axis=1, inplace=True)

In [122]:
df.null.value_counts()

TypeError: unhashable type: 'list'

Exception ignored in: 'pandas._libs.index.IndexEngine._call_map_locations'
Traceback (most recent call last):
  File "pandas\_libs\hashtable_class_helper.pxi", line 1652, in pandas._libs.hashtable.PyObjectHashTable.map_locations
TypeError: unhashable type: 'list'


[]    15919
Name: null, dtype: int64

In [123]:
df.drop('null', axis=1, inplace=True)

In [124]:
df['Next Inspection'] = df['Next Inspection'].astype(str)

In [125]:
type(df['Next Inspection'][0])

str

In [126]:
next_ins = df['Next Inspection'].str.extract('(\d\d/\d\d\d\d)')

In [127]:
next_ins.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 15919 entries, 0 to 15918
Data columns (total 1 columns):
 #   Column  Non-Null Count  Dtype 
---  ------  --------------  ----- 
 0   0       3535 non-null   object
dtypes: object(1)
memory usage: 124.5+ KB


In [128]:
df['Next Inspection'] = next_ins

In [129]:
df['Next Inspection']

0        06/2021
1            NaN
2            NaN
3            NaN
4            NaN
5            NaN
6            NaN
7            NaN
8        02/2020
9            NaN
10           NaN
11           NaN
12       09/2019
13           NaN
14       10/2019
15       04/2020
16           NaN
17           NaN
18       07/2020
19           NaN
20           NaN
21           NaN
22       12/2019
23           NaN
24           NaN
25           NaN
26           NaN
27           NaN
28           NaN
29           NaN
30           NaN
31       05/2019
32           NaN
33           NaN
34           NaN
35           NaN
36           NaN
37       07/2019
38       10/2019
39           NaN
40           NaN
41           NaN
42           NaN
43           NaN
44       02/2021
45       06/2019
46           NaN
47           NaN
48           NaN
49           NaN
50           NaN
51       06/2019
52           NaN
53           NaN
54           NaN
55       05/2020
56       11/2019
57       06/2021
58       12/20

In [130]:
df['Make'].value_counts()

\nOpel\n       7343
\nAudi\n       5712
\nRenault\n    2864
Name: Make, dtype: int64

In [131]:
df.Make[df.Make == '\nOpel\n'] = 'Opel'

In [132]:
df.Make[df.Make == '\nAudi\n'] = 'Audi'

In [133]:
df.Make[df.Make == '\nRenault\n'] = 'Renault'

In [134]:
df['Make'].value_counts()

Opel       7343
Audi       5712
Renault    2864
Name: Make, dtype: int64

In [135]:
df['Model'].value_counts(3)

TypeError: unhashable type: 'list'

Exception ignored in: 'pandas._libs.index.IndexEngine._call_map_locations'
Traceback (most recent call last):
  File "pandas\_libs\hashtable_class_helper.pxi", line 1652, in pandas._libs.hashtable.PyObjectHashTable.map_locations
TypeError: unhashable type: 'list'


[\n, A3, \n]          0.194547
[\n, A1, \n]          0.164206
[\n, Insignia, \n]    0.163201
[\n, Astra, \n]       0.158678
[\n, Corsa, \n]       0.139393
[\n, Clio, \n]        0.115522
[\n, Espace, \n]      0.062253
[\n, Duster, \n]      0.002136
[\n, A2, \n]          0.000063
Name: Model, dtype: float64

In [136]:
df['Model'].notnull().sum()

15919

In [137]:
model = df['Model'].str.extract('(\w{2,})')

In [138]:
model.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 15919 entries, 0 to 15918
Data columns (total 1 columns):
 #   Column  Non-Null Count  Dtype 
---  ------  --------------  ----- 
 0   0       0 non-null      object
dtypes: object(1)
memory usage: 124.5+ KB


In [139]:
df['Model'].astype('str')

0              ['\n', 'A1', '\n']
1              ['\n', 'A1', '\n']
2              ['\n', 'A1', '\n']
3              ['\n', 'A1', '\n']
4              ['\n', 'A1', '\n']
5              ['\n', 'A1', '\n']
6              ['\n', 'A1', '\n']
7              ['\n', 'A1', '\n']
8              ['\n', 'A1', '\n']
9              ['\n', 'A1', '\n']
10             ['\n', 'A1', '\n']
11             ['\n', 'A1', '\n']
12             ['\n', 'A1', '\n']
13             ['\n', 'A1', '\n']
14             ['\n', 'A1', '\n']
15             ['\n', 'A1', '\n']
16             ['\n', 'A1', '\n']
17             ['\n', 'A1', '\n']
18             ['\n', 'A1', '\n']
19             ['\n', 'A1', '\n']
20             ['\n', 'A1', '\n']
21             ['\n', 'A1', '\n']
22             ['\n', 'A1', '\n']
23             ['\n', 'A1', '\n']
24             ['\n', 'A1', '\n']
25             ['\n', 'A1', '\n']
26             ['\n', 'A1', '\n']
27             ['\n', 'A1', '\n']
28             ['\n', 'A1', '\n']
29            

In [140]:
type(df.Model[1])

list

In [141]:
df['Model']= df['Model'].str.extract('(\w{2,})')

In [142]:
df['Model'].head(10) # Bu niye NaN veriyor?

0    NaN
1    NaN
2    NaN
3    NaN
4    NaN
5    NaN
6    NaN
7    NaN
8    NaN
9    NaN
Name: Model, dtype: object

In [143]:
df['Offer Number'] = df['Offer Number'].astype('str')

In [144]:
df[['Offer Number']].head(10)

Offer Number
0  ['\nLR-062483\n']
1                nan
2   ['\nAM-95365\n']
3                nan
4      ['\nC1626\n']
5    ['\nJV03654\n']
6     ['\n200-19\n']
7  ['\n18381A-Q2\n']
8   ['\n11540324\n']
9                nan

In [145]:
df['Offer Number'] = [item.strip(' []\'\\n') for item in df['Offer Number']] 

In [146]:
df[['Offer Number']].head(10)

Offer Number
0    LR-062483
1            a
2     AM-95365
3            a
4        C1626
5      JV03654
6       200-19
7    18381A-Q2
8     11540324
9            a

In [147]:
df['Offer Number'][df['Offer Number']=='a'] = np.nan

In [148]:
df[['Offer Number']].head(10)

Offer Number
0    LR-062483
1          NaN
2     AM-95365
3          NaN
4        C1626
5      JV03654
6       200-19
7    18381A-Q2
8     11540324
9          NaN

In [149]:
df['First Registration'].head(10)

0    [\n, 2016, \n]
1    [\n, 2017, \n]
2    [\n, 2016, \n]
3    [\n, 2016, \n]
4    [\n, 2016, \n]
5    [\n, 2016, \n]
6    [\n, 2016, \n]
7    [\n, 2016, \n]
8    [\n, 2016, \n]
9    [\n, 2017, \n]
Name: First Registration, dtype: object

In [150]:
df['First Registration'] = [item.strip(' \\n,') for item in df['First Registration']] #Burada niye list object?

AttributeError: 'list' object has no attribute 'strip'

In [ ]:
df['First Registration'].str.extract('(\d{4})').head(10) #Bu niye NaN veriyor? Regex101 e gore dogru regex kodu var.

In [ ]:
df['First Registration'] = df['First Registration'].astype('str')

In [ ]:
df['First Registration'].head()

In [ ]:
df['First Registration'][0]

In [ ]:
df['First Registration'] = df['First Registration'].apply(lambda line: line.split()[0][1])

In [ ]:
df['First Registration'].head()

In [ ]:
df['Body Color'].head(10)

In [ ]:
df['Body Color'].str.extract('(\w{2,})')

In [ ]:
df.head()

**Comfort & Convenience**

In [ ]:
df['\nComfort & Convenience\n'][0]

In [ ]:
def unique_values(df, column_name):
    uni_val = set()
    for rows in df[column_name]:
        uni_val.update(rows)
    return list(uni_val)
    

In [ ]:
df.loc[df['\nComfort & Convenience\n'].isnull()]['\nComfort & Convenience\n']

In [ ]:
def Nan_to_list(data, column_name):
    NaN_rows = data[column_name].isnull()
    data.loc[NaN_rows, column_name] = data.loc[NaN_rows, column_name].apply (lambda x: [])

In [ ]:
Nan_to_list(df, '\nComfort & Convenience\n')
unique_values(df, '\nComfort & Convenience\n')

In [ ]:
str_list = [', '.join(item) if type(item) == list else item for item in df['\nComfort & Convenience\n']] 

In [ ]:
df['Comfort&Convenience'] = str_list

In [151]:
df['Comfort&Convenience'].value_counts(dropna=False)

KeyError: 'Comfort&Convenience'

In [ ]:
df['Comfort&Convenience'].isnull().sum()

In [152]:
[np.nan if df['Comfort&Convenience'].iloc[i]=='' else df['Comfort&Convenience'].iloc[i] for i in range(len(df['Comfort&Convenience']))]

KeyError: 'Comfort&Convenience'

In [153]:
df['Comfort&Convenience'] = [np.nan if df['Comfort&Convenience'].iloc[i]=='' else df['Comfort&Convenience'].iloc[i] for i in range(len(df['Comfort&Convenience']))]

KeyError: 'Comfort&Convenience'

In [ ]:
df['Comfort&Convenience'].isnull().sum()

In [154]:
fill_most(df, 'make_model','Comfort&Convenience')

KeyError: 'Comfort&Convenience'

In [155]:
car['hp2'] = car['hp2'].fillna(car.groupby('model1')['hp2'].apply(lambda x: x.fillna(x.mode()[0])))

NameError: name 'car' is not defined

In [156]:
df['\nEntertainment & Media\n'][0]

['Bluetooth', 'Hands-free equipment', 'On-board computer', 'Radio']

In [157]:
df['\nEntertainment & Media\n'] = [', '.join(item) if type(item) == list else item for item in df['\nEntertainment & Media\n']] 

In [158]:
df['\nEntertainment & Media\n'][0]

'Bluetooth, Hands-free equipment, On-board computer, Radio'

In [159]:
df.rename(columns={'\nEntertainment & Media\n':'Entertainment & Media'}, inplace=True)

In [160]:
df.rename(columns={'\nComfort & Convenience\n':'Comfort & Convenience'}, inplace=True)

In [161]:
df.rename(columns={'\nExtras\n':'Extras'}, inplace=True)

In [162]:
df.rename(columns={'\nSafety & Security\n':'Safety & Security'}, inplace=True)

In [163]:
df['Extras'][0]

['Alloy wheels', 'Catalytic Converter', 'Voice Control']

In [164]:
df['Extras'] = [', '.join(item) if type(item) == list else item for item in df['Extras']] 

In [165]:
df['Extras'][0]

'Alloy wheels, Catalytic Converter, Voice Control'

In [166]:
df['Safety & Security'][0]

['ABS',
 'Central door lock',
 'Daytime running lights',
 'Driver-side airbag',
 'Electronic stability control',
 'Fog lights',
 'Immobilizer',
 'Isofix',
 'Passenger-side airbag',
 'Power steering',
 'Side airbag',
 'Tire pressure monitoring system',
 'Traction control',
 'Xenon headlights']

In [167]:
df['Safety & Security'] = [', '.join(item) if type(item) == list else item for item in df['Safety & Security']] 

In [168]:
df.loc[:, ['make_model', 'Safety & Security']].head(20)

make_model                                  Safety & Security
0     Audi A1  ABS, Central door lock, Daytime running lights...
1     Audi A1  ABS, Central door lock, Central door lock with...
2     Audi A1  ABS, Central door lock, Daytime running lights...
3     Audi A1  ABS, Alarm system, Central door lock with remo...
4     Audi A1  ABS, Central door lock, Driver-side airbag, El...
5     Audi A1  ABS, Central door lock, Daytime running lights...
6     Audi A1  ABS, Central door lock, Daytime running lights...
7     Audi A1  ABS, Central door lock, Daytime running lights...
8     Audi A1  ABS, Central door lock, Driver-side airbag, El...
9     Audi A1                                                NaN
10    Audi A1  ABS, Central door lock, Daytime running lights...
11    Audi A1  ABS, Central door lock, Daytime running lights...
12    Audi A1  ABS, Central door lock, Daytime running lights...
13    Audi A1  ABS, Adaptive headlights, Central door lock, D...
14    Audi A1  ABS, Central door lock, Daytime running lights...
15    Audi A1  ABS, Central door lock, Daytime running lights...
16    Audi A1  Central door lock, Driver-side airbag, Electro...
17    Audi A1  ABS, Alarm system, Central door lock, Central ...
18    Audi A1  ABS, Central door lock, Daytime running lights...
19    Audi A1  Alarm system, Central door lock, Daytime runni...

In [169]:
df[df['Safety & Security'].isnull()]['make_model']

9               Audi A1
30              Audi A1
53              Audi A1
168             Audi A1
191             Audi A1
277             Audi A1
406             Audi A1
407             Audi A1
480             Audi A1
505             Audi A1
532             Audi A1
595             Audi A1
741             Audi A1
769             Audi A1
774             Audi A1
776             Audi A1
778             Audi A1
787             Audi A1
796             Audi A1
798             Audi A1
810             Audi A1
811             Audi A1
819             Audi A1
843             Audi A1
895             Audi A1
908             Audi A1
921             Audi A1
922             Audi A1
930             Audi A1
946             Audi A1
956             Audi A1
986             Audi A1
1012            Audi A1
1025            Audi A1
1038            Audi A1
1125            Audi A1
1140            Audi A1
1149            Audi A1
1152            Audi A1
1168            Audi A1
1262            Audi A1
1269            

In [170]:
type(df['description'][0])

list

In [171]:
df['description'] = [', '.join(item) if type(item) == list else item for item in df['description']] 

In [172]:
df['description'] = [' '.join(i.split()).replace(', ,', '') for i in df['description']]

In [173]:
df['description'][0]

', Sicherheit: Deaktivierung für Beifahrer-Airbag ESC mit elektronischer Quersperre Tagfahrlicht Reifendruck-Kontrollanzeige Kopfairbag-System mit Seiten-Airbags vorn Sicherheitslenksäule, Assistenzsysteme: Berganfahrassistent, Komfort: Scheinwerferreinigung Xenon plus inklusive Scheinwerfer-Reinigungsanlage Scheinwerfer-Reinigungsanlage Einparkhilfe hinten Licht-/Regensensor Funkfernbedienung Elektrische Luftzusatzheizung, Interieur: Rücksitzanlage 2 + 1 Multifunktions-Sportlederlenkrad im 3-Speichen-Design automatische Leuchtweitenregulierung Fahrerinformationssystem Staub- und Pollenfilter Kopfstützen hinten (3 Stück) Stoff Zeitgeist Fahrersitz manuell höheneinstellbar Scheiben seitlich und hinten in Wärmeschutzverglasung Kindersitzbefestigung ISOFIX und Top Tether für die äußeren Fondsitze Dachhimmel in Stoff titangrau Waschwasser-Standanzeige Nichtraucherfahrzeug, Exterieur: Elektrische Aussenspiegel Außenspiegel elektrisch beheizbar inklusive beheizbarer Scheibenwaschdüsen Scheib

In [174]:
# get_dummies cok fazla unique degeri olan sutunlarda sorun cikarmaz mi?
# tum NaN degerleri yok etmeye calismak sorun cikarmaz mi?

In [175]:
df.Consumption.str[0].sample(50)

5573     [4.5 l/100 km (comb)]
12532      [5 l/100 km (comb)]
2125     [4.8 l/100 km (comb)]
6010                       NaN
7535                        \n
7829                       NaN
14615    [5.6 l/100 km (comb)]
14208      [5 l/100 km (comb)]
10364    [5.6 l/100 km (comb)]
1441     [4.4 l/100 km (comb)]
15018    [6.8 l/100 km (comb)]
7004     [3.7 l/100 km (comb)]
7965     [4.9 l/100 km (comb)]
3850       [3 l/100 km (comb)]
1505     [3.9 l/100 km (comb)]
13257      [3 l/100 km (comb)]
15056    [4.6 l/100 km (comb)]
15493      [5 l/100 km (comb)]
10815    [5.1 l/100 km (comb)]
5577       [5 l/100 km (comb)]
13206    [3.5 l/100 km (comb)]
6849     [3.4 l/100 km (comb)]
7790     [5.5 l/100 km (comb)]
14271                      NaN
5998     [4.5 l/100 km (comb)]
12121                       \n
4935     [4.1 l/100 km (comb)]
4166       [4 l/100 km (comb)]
12494    [7.1 l/100 km (comb)]
9531     [5.2 l/100 km (comb)]
15778                      NaN
7948     [5.6 l/100 km (comb)]
14469   

In [176]:
df.Consumption.str[0].str[0].value_counts(dropna=False)

NaN                     2033
\n                       850
3.9 l/100 km (comb)      732
4 l/100 km (comb)        712
5.4 l/100 km (comb)      662
5.1 l/100 km (comb)      627
4.4 l/100 km (comb)      595
3.8 l/100 km (comb)      585
5.6 l/100 km (comb)      568
4.7 l/100 km (comb)      555
4.8 l/100 km (comb)      523
5 l/100 km (comb)        513
4.5 l/100 km (comb)      511
5.2 l/100 km (comb)      429
4.6 l/100 km (comb)      420
4.2 l/100 km (comb)      408
5.3 l/100 km (comb)      374
3.7 l/100 km (comb)      369
4.9 l/100 km (comb)      348
5.5 l/100 km (comb)      342
4.1 l/100 km (comb)      341
5.9 l/100 km (comb)      308
5.7 l/100 km (comb)      302
3.3 l/100 km (comb)      298
4.3 l/100 km (comb)      295
3.5 l/100 km (comb)      285
6 l/100 km (comb)        278
3.6 l/100 km (comb)      193
6.2 l/100 km (comb)      184
5.8 l/100 km (comb)      142
6.3 l/100 km (comb)      141
6.1 l/100 km (comb)      135
6.8 l/100 km (comb)      134
6.6 l/100 km (comb)      119
3.4 l/100 km (

In [177]:
df.Consumption.str[0].unique()

TypeError: unhashable type: 'list'

In [178]:
df['Consumption_comb'] = df.Consumption.str[0].str[0].str.extract('(\d.\d|\d)')

In [179]:
df['Consumption_comb'].value_counts(dropna=False)

NaN    2883
3.9     732
4       716
5.4     663
5.1     630
4.4     595
3.8     585
5.6     568
4.7     555
4.8     523
5       520
4.5     511
5.2     429
4.6     420
4.2     408
5.3     375
3.7     369
4.9     348
5.5     342
4.1     341
5.9     308
3.3     307
5.7     302
4.3     295
3.5     288
6       278
3.6     194
6.2     184
5.8     142
6.3     141
6.1     135
6.8     134
6.6     119
3.4     106
3        73
6.4      64
7.4      62
7.1      38
1        37
6.5      36
6.7      33
3.2      25
6.9      21
8.3      20
7.6      14
7         9
3.1       7
7.2       6
7.8       6
8         5
8.6       3
8.7       3
0         2
8.1       2
7.9       2
7.3       2
7.5       1
1.2       1
9.1       1
Name: Consumption_comb, dtype: int64

In [180]:
cons1 = df.Consumption.str[1].str.extract('(\d.\d|\d)')

In [181]:
cons1.head()

0
0  NaN
1  NaN
2  NaN
3  NaN
4  NaN

In [182]:
cons1[0].value_counts(dropna=False)

NaN    15069
5.4      107
5.9       61
6         53
5.6       50
4.7       47
4.9       45
5.7       40
6.1       40
6.3       40
5.5       38
5         32
6.2       32
6.6       29
4.4       28
5.1       27
4.2       27
5.2       25
4.8       23
5.8       22
4.5       12
4.3       12
6.4       11
6.7       10
6.5        7
4.6        6
6.9        6
5.3        5
7.4        4
1.6        3
6.8        2
7.9        1
4          1
8.6        1
3.9        1
4.1        1
7          1
Name: 0, dtype: int64

In [183]:
cons1[0].value_counts().sum()

850

In [184]:
df.Consumption_comb.fillna(cons1[0], inplace = True)

In [185]:
df.Consumption_comb.value_counts(dropna=False)

NaN    2033
5.4     770
3.9     733
4       717
5.1     657
4.4     623
5.6     618
4.7     602
3.8     585
5       552
4.8     546
4.5     523
5.2     454
4.2     435
4.6     426
4.9     393
5.5     380
5.3     380
3.7     369
5.9     369
4.1     342
5.7     342
6       331
4.3     307
3.3     307
3.5     288
6.2     216
3.6     194
6.3     181
6.1     175
5.8     164
6.6     148
6.8     136
3.4     106
6.4      75
3        73
7.4      66
6.5      43
6.7      43
7.1      38
1        37
6.9      27
3.2      25
8.3      20
7.6      14
7        10
3.1       7
7.2       6
7.8       6
8         5
8.6       4
7.9       3
8.7       3
1.6       3
7.3       2
0         2
8.1       2
7.5       1
1.2       1
9.1       1
Name: Consumption_comb, dtype: int64

In [186]:
df.Consumption.str[1].value_counts(dropna=False)

TypeError: unhashable type: 'list'

Exception ignored in: 'pandas._libs.index.IndexEngine._call_map_locations'
Traceback (most recent call last):
  File "pandas\_libs\hashtable_class_helper.pxi", line 1652, in pandas._libs.hashtable.PyObjectHashTable.map_locations
TypeError: unhashable type: 'list'


NaN                        1906
[5 l/100 km (city)]         642
[5.8 l/100 km (city)]       597
[4.5 l/100 km (city)]       577
[]                          516
[4.3 l/100 km (city)]       512
[5.1 l/100 km (city)]       470
[6.8 l/100 km (city)]       442
[4.6 l/100 km (city)]       417
[7.2 l/100 km (city)]       397
[5.7 l/100 km (city)]       365
[7.3 l/100 km (city)]       354
[4.2 l/100 km (city)]       353
[5.9 l/100 km (city)]       344
[7.8 l/100 km (city)]       341
[6.6 l/100 km (city)]       337
[5.2 l/100 km (city)]       333
[4.1 l/100 km (city)]       320
[6.3 l/100 km (city)]       317
[4 l/100 km (city)]         300
[5.4 l/100 km (city)]       289
[4.7 l/100 km (city)]       288
[6.7 l/100 km (city)]       286
[3.9 l/100 km (city)]       245
[6 l/100 km (city)]         239
[3.5 l/100 km (city)]       230
[7.6 l/100 km (city)]       227
[7.1 l/100 km (city)]       221
[7.5 l/100 km (city)]       217
[6.9 l/100 km (city)]       215
[5.5 l/100 km (city)]       207
[6.2 l/1

In [187]:
con_city= df.Consumption.str[-2].str[0].str.extract('(\d.\d|\d)')

In [188]:
con_city = pd.to_numeric(con_city[0])

In [189]:
con_country= df.Consumption.str[-1].str[0].str.extract('(\d.\d|\d)')

In [190]:
con_country = pd.to_numeric(con_country[0])

In [191]:
con_country

0        3.5
1        4.7
2        3.4
3        3.5
4        3.8
5        3.1
6        3.4
7        3.4
8        3.4
9        NaN
10       3.6
11       4.2
12       4.2
13       NaN
14       3.7
15       3.4
16       3.1
17       3.5
18       3.9
19       3.3
20       3.6
21       4.2
22       4.2
23       3.4
24       3.8
25       3.7
26       3.7
27       3.7
28       3.5
29       3.9
30       3.0
31       3.3
32       3.9
33       3.1
34       3.4
35       3.9
36       3.9
37       3.1
38       3.7
39       NaN
40       3.9
41       3.1
42       3.1
43       NaN
44       3.3
45       3.7
46       3.4
47       3.1
48       3.9
49       3.9
50       NaN
51       3.7
52       3.7
53       3.0
54       3.5
55       3.9
56       3.7
57       3.9
58       3.5
59       3.7
60       3.4
61       NaN
62       3.7
63       3.4
64       3.6
65       3.8
66       NaN
67       NaN
68       3.8
69       3.9
70       NaN
71       4.4
72       3.8
73       3.8
74       3.9
75       3.4
76       3.8

In [192]:
con2= (con_city + con_country)/2

In [193]:
df.Consumption_comb.fillna(con2, inplace = True)

In [194]:
df.Consumption_comb.value_counts(dropna=False)

NaN                   1925
5.4                    770
3.9                    733
4                      717
5.1                    657
4.4                    623
5.6                    618
4.7                    602
3.8                    585
5                      552
4.8                    546
4.5                    523
5.2                    454
4.2                    435
4.6                    426
4.9                    393
5.5                    380
5.3                    380
3.7                    369
5.9                    369
4.1                    342
5.7                    342
6                      331
4.3                    307
3.3                    307
3.5                    288
6.2                    216
3.6                    194
6.3                    181
6.1                    175
5.8                    164
6.6                    148
6.8                    136
3.4                    106
6.4                     75
3                       73
7.4                     66
6

**Gearing Type**

In [198]:
df['gearing_type']=df['Gearing Type'].str[1]

**Drive Chain**

In [199]:
df['drive_chain'] = df['Drive chain'].str[0].str.strip('\n')

**Model Code**

In [200]:
df['Model Code'].str[0].str.strip('\n')

0        0588/BDF
1        0588/BCY
2             NaN
3             NaN
4        0588/BDF
5             NaN
6             NaN
7        0588/BDF
8             NaN
9             NaN
10            NaN
11       0588/BDC
12       0588/BDC
13            NaN
14       0588/BDB
15            NaN
16            NaN
17            NaN
18            NaN
19            NaN
20            NaN
21       0588/BDC
22            NaN
23            NaN
24            NaN
25       0588/BDB
26       0588/BCV
27            NaN
28            NaN
29            NaN
30            NaN
31       0588/BCZ
32       0588/BCV
33            NaN
34            NaN
35       0588/BCV
36       0588/BCV
37            NaN
38            NaN
39            NaN
40       0588/BHL
41       0588/BDF
42       0588/BDF
43            NaN
44       0588/BCZ
45       0588/BCV
46            NaN
47            NaN
48            NaN
49       0588/BHL
50       0588/BDF
51       0588/BDB
52       0588/BDB
53            NaN
54       0588/BCZ
55       0

In [201]:
df.drop('Model Code', axis = 1, inplace=True)

**Body Color**

In [203]:
df['body_color']=df['Body Color'].str[1].str.strip()

In [205]:
df.body_color.fillna(method='bfill', inplace=True)

In [206]:
df.body_color.value_counts(dropna=False)

Black     3888
Grey      3638
White     3540
Silver    1687
Blue      1524
Red        989
Brown      299
Green      163
Beige      108
Yellow      53
Violet      18
Bronze       7
Orange       3
Gold         2
Name: body_color, dtype: int64

**Body Color Original**

In [209]:
df.drop('Body Color Original', axis = 1, inplace=True)

**CO2 Emmission**

In [211]:
df['CO2 Emission'].str[0].str.strip('\n')

0            99 g CO2/km (comb)
1           129 g CO2/km (comb)
2            99 g CO2/km (comb)
3            99 g CO2/km (comb)
4           109 g CO2/km (comb)
5            92 g CO2/km (comb)
6            98 g CO2/km (comb)
7            97 g CO2/km (comb)
8            97 g CO2/km (comb)
9                           NaN
10          105 g CO2/km (comb)
11          112 g CO2/km (comb)
12          112 g CO2/km (comb)
13                          NaN
14           99 g CO2/km (comb)
15           97 g CO2/km (comb)
16           92 g CO2/km (comb)
17           99 g CO2/km (comb)
18          103 g CO2/km (comb)
19           99 g CO2/km (comb)
20          105 g CO2/km (comb)
21          112 g CO2/km (comb)
22          112 g CO2/km (comb)
23           97 g CO2/km (comb)
24          102 g CO2/km (comb)
25           97 g CO2/km (comb)
26           97 g CO2/km (comb)
27           97 g CO2/km (comb)
28           99 g CO2/km (comb)
29          102 g CO2/km (comb)
30                          NaN
31      

In [213]:
df['CO2 Emission'].str[0].str.strip('\n').str.replace(",","").unique()

array(['99 g CO2/km (comb)', '129 g CO2/km (comb)', '109 g CO2/km (comb)',
       '92 g CO2/km (comb)', '98 g CO2/km (comb)', '97 g CO2/km (comb)',
       nan, '105 g CO2/km (comb)', '112 g CO2/km (comb)',
       '103 g CO2/km (comb)', '102 g CO2/km (comb)', '95 g CO2/km (comb)',
       '104 g CO2/km (comb)', '91 g CO2/km (comb)', '94 g CO2/km (comb)',
       '117 g CO2/km (comb)', '123 g CO2/km (comb)',
       '106 g CO2/km (comb)', '108 g CO2/km (comb)',
       '121 g CO2/km (comb)', '107 g CO2/km (comb)',
       '101 g CO2/km (comb)', '113 g CO2/km (comb)',
       '137 g CO2/km (comb)', '100 g CO2/km (comb)',
       '116 g CO2/km (comb)', '114 g CO2/km (comb)',
       '118 g CO2/km (comb)', '331 g CO2/km (comb)',
       '115 g CO2/km (comb)', '119 g CO2/km (comb)', '90 g CO2/km (comb)',
       '136 g CO2/km (comb)', '134 g CO2/km (comb)',
       '110 g CO2/km (comb)', '111 g CO2/km (comb)',
       '120 g CO2/km (comb)', '89 g CO2/km (comb)', '142 g CO2/km (comb)',
       '126 g CO2/

In [228]:
pattern = "(\d{1,5})"

In [229]:
df['co2_emmission'] = df['CO2 Emission'].str[0].str.strip('\n').str.replace(",","").str.extract(pattern)

In [230]:
df['co2_emmission'].value_counts(dropna=False)

NaN      2436
120       740
99        545
97        537
104       501
102       477
103       445
114       382
124       372
107       362
108       362
119       361
106       349
128       329
126       282
85        275
118       270
110       266
127       257
117       254
111       237
113       235
109       234
139       224
140       218
129       213
105       202
135       202
92        198
130       180
123       178
150       174
143       171
112       171
95        161
116       157
141       156
98        151
136       145
133       145
137       133
125       132
134       130
145       126
149       117
153       113
147       109
101       105
132       100
115        86
122        83
121        82
138        75
93         66
142        58
168        58
131        48
148        48
154        40
144        40
94         37
146        36
100        36
90         35
151        34
91         31
186        30
152        28
187        26
172        25
82         25
96    

In [232]:
df.co2_emmission.fillna(df.co2_emmission.median(), inplace=True)

In [233]:
df['co2_emmission'].value_counts(dropna=False)

116.0    2436
120       740
99        545
97        537
104       501
102       477
103       445
114       382
124       372
107       362
108       362
119       361
106       349
128       329
126       282
85        275
118       270
110       266
127       257
117       254
111       237
113       235
109       234
139       224
140       218
129       213
105       202
135       202
92        198
130       180
123       178
150       174
143       171
112       171
95        161
116       157
141       156
98        151
133       145
136       145
137       133
125       132
134       130
145       126
149       117
153       113
147       109
101       105
132       100
115        86
122        83
121        82
138        75
93         66
142        58
168        58
131        48
148        48
154        40
144        40
94         37
146        36
100        36
90         35
151        34
91         31
186        30
152        28
187        26
172        25
82         25
96    

**Displacement**

In [31]:
df.loc[:, ['make_model', 'Safety & Security']].head(10)

KeyError: 'Passing list-likes to .loc or [] with any missing labels is no longer supported, see https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#deprecate-loc-reindex-listlike'

In [32]:
# Her arabanin safety ve security donanimi farkli olabilir.

In [33]:
df.head()

url make_model  \
0  https://www.autoscout24.com//offers/audi-a1-sp...    Audi A1   
1  https://www.autoscout24.com//offers/audi-a1-1-...    Audi A1   
2  https://www.autoscout24.com//offers/audi-a1-sp...    Audi A1   
3  https://www.autoscout24.com//offers/audi-a1-1-...    Audi A1   
4  https://www.autoscout24.com//offers/audi-a1-sp...    Audi A1   

                                   short_description body_type  price  \
0        Sportback 1.4 TDI S-tronic Xenon Navi Klima    Sedans  15770   
1                                     1.8 TFSI sport    Sedans  14500   
2  Sportback 1.6 TDI S tronic Einparkhilfe plus+m...    Sedans  14640   
3                            1.4 TDi Design S tronic    Sedans  14500   
4  Sportback 1.4 TDI S-Tronic S-Line Ext. admired...    Sedans  16790   

                vat         km registration prev_owner      hp  ...  \
0    VAT deductible  56,013 km      01/2016          2   66 kW  ...   
1  Price negotiable  80,000 km      03/2017          1  141 kW  ...   
2    VAT deductible  83,450 km      02/2016          1   85 kW  ...   
3              None  73,000 km      08/2016          1   66 kW  ...   
4              None  16,200 km      05/2016          1   66 kW  ...   

                CO2 Emission Emission Class  \
0   [\n99 g CO2/km (comb)\n]   [\nEuro 6\n]   
1  [\n129 g CO2/km (comb)\n]   [\nEuro 6\n]   
2   [\n99 g CO2/km (comb)\n]   [\nEuro 6\n]   
3   [\n99 g CO2/km (comb)\n]   [\nEuro 6\n]   
4  [\n109 g CO2/km (comb)\n]   [\nEuro 6\n]   

                           \nComfort & Convenience\n  \
0  [Air conditioning, Armrest, Automatic climate ...   
1  [Air conditioning, Automatic climate control, ...   
2  [Air conditioning, Cruise control, Electrical ...   
3  [Air suspension, Armrest, Auxiliary heating, E...   
4  [Air conditioning, Armrest, Automatic climate ...   

                           \nEntertainment & Media\n  \
0  [Bluetooth, Hands-free equipment, On-board com...   
1  [Bluetooth, Hands-free equipment, On-board com...   
2                           [MP3, On-board computer]   
3  [Bluetooth, CD player, Hands-free equipment, M...   
4  [Bluetooth, CD player, Hands-free equipment, M...   

                                          \nExtras\n  \
0  [Alloy wheels, Catalytic Converter, Voice Cont...   
1  [Alloy wheels, Sport seats, Sport suspension, ...   
2                      [Alloy wheels, Voice Control]   
3         [Alloy wheels, Sport seats, Voice Control]   
4  [Alloy wheels, Sport package, Sport suspension...   

                               \nSafety & Security\n  \
0  [ABS, Central door lock, Daytime running light...   
1  [ABS, Central door lock, Central door lock wit...   
2  [ABS, Central door lock, Daytime running light...   
3  [ABS, Alarm system, Central door lock with rem...   
4  [ABS, Central door lock, Driver-side airbag, E...   

                                         description   Emission Label  \
0  [\n, Sicherheit:,  , Deaktivierung für Beifahr...              NaN   
1  [\nLangstreckenfahrzeug daher die hohe Kilomet...  [\n4 (Green)\n]   
2  [\n, Fahrzeug-Nummer: AM-95365,  , Ehem. UPE 2...  [\n4 (Green)\n]   
3  [\nAudi A1: , - 1e eigenaar , - Perfecte staat...              NaN   
4  [\n, Technik & Sicherheit:, Xenon plus, Klimaa...              NaN   

     Gears Country version  
0      NaN             NaN  
1  [\n7\n]             NaN  
2      NaN             NaN  
3  [\n6\n]             NaN  
4      NaN   [\nGermany\n]  

[5 rows x 45 columns]

In [34]:
df['make_model'] = pd.get_dummies(df['make_model'])  #hepsini bir yapti bi sorun var?

In [35]:
df.head()

url  make_model  \
0  https://www.autoscout24.com//offers/audi-a1-sp...           1   
1  https://www.autoscout24.com//offers/audi-a1-1-...           1   
2  https://www.autoscout24.com//offers/audi-a1-sp...           1   
3  https://www.autoscout24.com//offers/audi-a1-1-...           1   
4  https://www.autoscout24.com//offers/audi-a1-sp...           1   

                                   short_description body_type  price  \
0        Sportback 1.4 TDI S-tronic Xenon Navi Klima    Sedans  15770   
1                                     1.8 TFSI sport    Sedans  14500   
2  Sportback 1.6 TDI S tronic Einparkhilfe plus+m...    Sedans  14640   
3                            1.4 TDi Design S tronic    Sedans  14500   
4  Sportback 1.4 TDI S-Tronic S-Line Ext. admired...    Sedans  16790   

                vat         km registration prev_owner      hp  ...  \
0    VAT deductible  56,013 km      01/2016          2   66 kW  ...   
1  Price negotiable  80,000 km      03/2017          1  141 kW  ...   
2    VAT deductible  83,450 km      02/2016          1   85 kW  ...   
3              None  73,000 km      08/2016          1   66 kW  ...   
4              None  16,200 km      05/2016          1   66 kW  ...   

                CO2 Emission Emission Class  \
0   [\n99 g CO2/km (comb)\n]   [\nEuro 6\n]   
1  [\n129 g CO2/km (comb)\n]   [\nEuro 6\n]   
2   [\n99 g CO2/km (comb)\n]   [\nEuro 6\n]   
3   [\n99 g CO2/km (comb)\n]   [\nEuro 6\n]   
4  [\n109 g CO2/km (comb)\n]   [\nEuro 6\n]   

                           \nComfort & Convenience\n  \
0  [Air conditioning, Armrest, Automatic climate ...   
1  [Air conditioning, Automatic climate control, ...   
2  [Air conditioning, Cruise control, Electrical ...   
3  [Air suspension, Armrest, Auxiliary heating, E...   
4  [Air conditioning, Armrest, Automatic climate ...   

                           \nEntertainment & Media\n  \
0  [Bluetooth, Hands-free equipment, On-board com...   
1  [Bluetooth, Hands-free equipment, On-board com...   
2                           [MP3, On-board computer]   
3  [Bluetooth, CD player, Hands-free equipment, M...   
4  [Bluetooth, CD player, Hands-free equipment, M...   

                                          \nExtras\n  \
0  [Alloy wheels, Catalytic Converter, Voice Cont...   
1  [Alloy wheels, Sport seats, Sport suspension, ...   
2                      [Alloy wheels, Voice Control]   
3         [Alloy wheels, Sport seats, Voice Control]   
4  [Alloy wheels, Sport package, Sport suspension...   

                               \nSafety & Security\n  \
0  [ABS, Central door lock, Daytime running light...   
1  [ABS, Central door lock, Central door lock wit...   
2  [ABS, Central door lock, Daytime running light...   
3  [ABS, Alarm system, Central door lock with rem...   
4  [ABS, Central door lock, Driver-side airbag, E...   

                                         description   Emission Label  \
0  [\n, Sicherheit:,  , Deaktivierung für Beifahr...              NaN   
1  [\nLangstreckenfahrzeug daher die hohe Kilomet...  [\n4 (Green)\n]   
2  [\n, Fahrzeug-Nummer: AM-95365,  , Ehem. UPE 2...  [\n4 (Green)\n]   
3  [\nAudi A1: , - 1e eigenaar , - Perfecte staat...              NaN   
4  [\n, Technik & Sicherheit:, Xenon plus, Klimaa...              NaN   

     Gears Country version  
0      NaN             NaN  
1  [\n7\n]             NaN  
2      NaN             NaN  
3  [\n6\n]             NaN  
4      NaN   [\nGermany\n]  

[5 rows x 45 columns]

In [36]:
df['short_description'][372]

In [37]:
def fill_most(x, y):
a = df[x][df['make_model'] == y].value_counts().index[0]
b = df[x][df['make_model'] == y]
b = b.apply(lambda z : z if isinstance(z, list) else a)
df[x][df['make_model'] == y] = b
x = doldurmak istediğimiz sütun
y = marka-model ismi (edited) 

IndentationError: expected an indented block (<ipython-input-37-e553ae84ef0b>, line 2)

In [38]:
for i in range(df['make_model'].nunique()):
    fill_most('Extras', df['make_model'].unique()[i])

NameError: name 'fill_most' is not defined